In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [5]:
neighborhoods_data = newyork_data['features']

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [8]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [10]:
# we'll choose manhatten city to work on as we already worked on 

In [11]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [12]:
CLIENT_ID = '55VFOGTCXVFDSLPDQ3EH14W3DELB4QQOMRVGDEW33I5SEOQ3' 
CLIENT_SECRET = 'T2F1UA3PQQX2AP1D5BLHFKIKMSMXSU3SJWCJOWK11DGMURXB'
VERSION = '20180605'# Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 55VFOGTCXVFDSLPDQ3EH14W3DELB4QQOMRVGDEW33I5SEOQ3
CLIENT_SECRET:T2F1UA3PQQX2AP1D5BLHFKIKMSMXSU3SJWCJOWK11DGMURXB


In [13]:
# we'll create a function to extrac all venues near to manhatten neighborhoods 

In [14]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [15]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )


Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [16]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3204, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

In [17]:
ddd = manhattan_venues

In [18]:
#let's see how many unique category we have that we will work on

In [19]:
pd.DataFrame(manhattan_venues['Venue Category'].unique())

0
0                                 Pizza Place
1                                 Yoga Studio
2                                       Diner
3                                  Donut Shop
4                                 Coffee Shop
5                                         Gym
6                                    Pharmacy
7                          Seafood Restaurant
8                              Tennis Stadium
9                            Department Store
10                             Discount Store
11                            Supplement Shop
12                             Sandwich Place
13                             Ice Cream Shop
14                           Video Game Store
15                                 Steakhouse
16                                 Kids Store
17                              Deli / Bodega
18                                      Hotel
19                         Chinese Restaurant
20                               Cocktail Bar
21                           Greek Restaurant
22                                     Bakery
23                                        Spa
24                          Hotpot Restaurant
25                            Bubble Tea Shop
26                               Noodle House
27                                     Museum
28                         Salon / Barbershop
29                               Dessert Shop
30                    New American Restaurant
31                        American Restaurant
32                        Indie Movie Theater
33                           Asian Restaurant
34                                   Tea Room
35                                  Roof Deck
36                         Spanish Restaurant
37                                  Bike Shop
38                                   Boutique
39                              Garden Center
40                     Furniture / Home Store
41                            Thai Restaurant
42                              Historic Site
43                            Organic Grocery
44                                Music Venue
45                         Italian Restaurant
46                                Supermarket
47                             Cosmetics Shop
48                         Dim Sum Restaurant
49                      Vietnamese Restaurant
50                        Shanghai Restaurant
51                         Mexican Restaurant
52                                Snack Place
53                           Malay Restaurant
54                                  Gift Shop
55              Paper / Office Supplies Store
56                               Optical Shop
57                       Taiwanese Restaurant
58                                Sports Club
59                        Dumpling Restaurant
60                        Austrian Restaurant
61                          Korean Restaurant
62                                 Shoe Store
63              Vegetarian / Vegan Restaurant
64                                        Bar
65                              Grocery Store
66                       Cantonese Restaurant
67                                 Restaurant
68                                       Café
69                                       Park
70                               Burger Joint
71                                     Market
72                                  Wine Shop
73                                   Pet Café
74                           Ramen Restaurant
75                               Liquor Store
76                             Breakfast Spot
77                           Tapas Restaurant
78                             Scenic Lookout
79                                       Pool
80                       Caribbean Restaurant
81                          Indian Restaurant
82                  Latin American Restaurant
83                                     Lounge
84                         Frozen Yogurt Shop
85                          Mobile Phone Shop
86                           Sushi Restaur

In [20]:
#Let's check how many venues were returned for each neighborhood

In [21]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       66                      66     66   
Carnegie Hill                           86                      86     86   
Central Harlem                          45                      45     45   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             40                      40     40   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                94                      94     94   
Greenwich Village                      100                     100    100   
Hamilton Heights                        63                      63     63   
Hudson Yards                            62                      62     62   
Inwood                                  57                      57     57   
Lenox Hill                             100                     100    100   
Lincoln Square                          92                      92     92   
Little Italy                           100                     100    100   
Lower East Side                         47                      47     47   
Manhattan Valley                        49                      49     49   
Manhattanville                          47                      47     47   
Marble Hill                             22                      22     22   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     43                      43     43   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        26                      26     26   
Soho                                   100                     100    100   
Stuyvesant Town                         17                      17     17   
Sutton Place                           100                     100    100   
Tribeca                                 88                      88     88   
Tudor City                              81                      81     81   
Turtle Bay                             100                     100    100   
Upper East Side                         97                      97     97   
Upper West Side                         98                      98     98   
Washington Heights                      84                      84     84   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                66               66              66  
Carnegie Hill                    86               86              86  
Central Harlem                   45               45              45  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      40               40              40  
East Village                    100              100             100  
Finan

## Processing Categories :

In [22]:
# to make the things simple, i'll work only on 6 categories "Gym" , "Restaurant" , "Shop" , "Hotel" , "Bar" and "Café"

#### we are going to assemble categories, for exemple if a category have the word "Restaurant" then it will become that name ("Fast Food Restaurant" will become "Restaurant")

In [23]:
# import re to use regular expressions

import re

In [24]:

for i in manhattan_venues.index:
    if re.search("Restaurant", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Restaurant"
    elif re.search("Gym", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Gym"
    elif re.search("Shop", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Shop"
    elif re.search("Hotel", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Hotel"    
    elif re.search("Bar", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Bar" 
    elif re.search("Café", manhattan_venues.loc[i,'Venue Category']):
        manhattan_venues.loc[i,'Venue Category'] = "Café" 

In [25]:
manhattan_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0             Marble Hill              40.876551              -73.910660   
1             Marble Hill              40.876551              -73.910660   
2             Marble Hill              40.876551              -73.910660   
3             Marble Hill              40.876551              -73.910660   
4             Marble Hill              40.876551              -73.910660   
5             Marble Hill              40.876551              -73.910660   
6             Marble Hill              40.876551              -73.910660   
7             Marble Hill              40.876551              -73.910660   
8             Marble Hill              40.876551              -73.910660   
9             Marble Hill              40.876551              -73.910660   
10            Marble Hill              40.876551              -73.910660   
11            Marble Hill              40.876551              -73.910660   
12            Marble Hill              40.876551              -73.910660   
13            Marble Hill              40.876551              -73.910660   
14            Marble Hill              40.876551              -73.910660   
15            Marble Hill              40.876551              -73.910660   
16            Marble Hill              40.876551              -73.910660   
17            Marble Hill              40.876551              -73.910660   
18            Marble Hill              40.876551              -73.910660   
19            Marble Hill              40.876551              -73.910660   
20            Marble Hill              40.876551              -73.910660   
21            Marble Hill              40.876551              -73.910660   
22              Chinatown              40.715618              -73.994279   
23              Chinatown              40.715618              -73.994279   
24              Chinatown              40.715618              -73.994279   
25              Chinatown              40.715618              -73.994279   
26              Chinatown              40.715618              -73.994279   
27              Chinatown              40.715618              -73.994279   
28              Chinatown              40.715618              -73.994279   
29              Chinatown              40.715618              -73.994279   
30              Chinatown              40.715618              -73.994279   
31              Chinatown              40.715618              -73.994279   
32              Chinatown              40.715618              -73.994279   
33              Chinatown              40.715618              -73.994279   
34              Chinatown              40.715618              -73.994279   
35              Chinatown              40.715618              -73.994279   
36              Chinatown              40.715618              -73.994279   
37              Chinatown              40.715618              -73.994279   
38              Chinatown              40.715618              -73.994279   
39              Chinatown              40.715618              -73.994279   
40              Chinatown              40.715618              -73.994279   
41              Chinatown              40.715618              -73.994279   
42              Chinatown              40.715618              -73.994279   
43              Chinatown              40.715618              -73.994279   
44              Chinatown              40.715618              -73.994279   
45              Chinatown              40.715618              -73.994279   
46              Chinatown              40.715618              -73.994279   
47              Chinatown              40.715618              -73.994279   
48              Chinatown              40.715618              -73.994279   
49              Chinatown              40.715618              -73.994279   
50              Chinatown              40.715618              -73.994279   
51              Chinatown              40.715618             

In [26]:
# we'll delete now the rows who don't have our category choices to make the plot more visible 

In [27]:
manhatten_reduced_ind = manhattan_venues[manhattan_venues['Venue Category'].values == "Restaurant"].index


In [28]:
manhatten_reduced_ind = np.array(manhatten_reduced_ind.to_list())

In [29]:
type(manhatten_reduced_ind)

numpy.ndarray

In [30]:
manhatten_reduced_ind = np.append(manhatten_reduced_ind,manhattan_venues[manhattan_venues['Venue Category'].values =="Bar"].index)
print(manhatten_reduced_ind.shape)
manhatten_reduced_ind = np.append(manhatten_reduced_ind,manhattan_venues[manhattan_venues['Venue Category'].values =="Hotel"].index)
print(manhatten_reduced_ind.shape)
manhatten_reduced_ind = np.append(manhatten_reduced_ind,manhattan_venues[manhattan_venues['Venue Category'].values =="Café"].index)
print(manhatten_reduced_ind.shape)
manhatten_reduced_ind = np.append(manhatten_reduced_ind,manhattan_venues[manhattan_venues['Venue Category'].values =="Gym"].index)
print(manhatten_reduced_ind.shape)
manhatten_reduced_ind = np.append(manhatten_reduced_ind,manhattan_venues[manhattan_venues['Venue Category'].values =="Shop"].index)
print(manhatten_reduced_ind.shape)

(1116,)
(1187,)
(1273,)
(1399,)
(1846,)


In [31]:
manhatten_reduced_ind.shape

(1846,)

In [32]:
manhattan_reduced = ddd.iloc[manhatten_reduced_ind ,]

In [33]:
manhattan_reduced

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
9             Marble Hill              40.876551              -73.910660   
24              Chinatown              40.715618              -73.994279   
27              Chinatown              40.715618              -73.994279   
29              Chinatown              40.715618              -73.994279   
32              Chinatown              40.715618              -73.994279   
35              Chinatown              40.715618              -73.994279   
39              Chinatown              40.715618              -73.994279   
41              Chinatown              40.715618              -73.994279   
44              Chinatown              40.715618              -73.994279   
47              Chinatown              40.715618              -73.994279   
54              Chinatown              40.715618              -73.994279   
55              Chinatown              40.715618              -73.994279   
59              Chinatown              40.715618              -73.994279   
62              Chinatown              40.715618              -73.994279   
63              Chinatown              40.715618              -73.994279   
66              Chinatown              40.715618              -73.994279   
67              Chinatown              40.715618              -73.994279   
68              Chinatown              40.715618              -73.994279   
69              Chinatown              40.715618              -73.994279   
70              Chinatown              40.715618              -73.994279   
72              Chinatown              40.715618              -73.994279   
76              Chinatown              40.715618              -73.994279   
78              Chinatown              40.715618              -73.994279   
79              Chinatown              40.715618              -73.994279   
81              Chinatown              40.715618              -73.994279   
84              Chinatown              40.715618              -73.994279   
85              Chinatown              40.715618              -73.994279   
88              Chinatown              40.715618              -73.994279   
91              Chinatown              40.715618              -73.994279   
92              Chinatown              40.715618              -73.994279   
95              Chinatown              40.715618              -73.994279   
97              Chinatown              40.715618              -73.994279   
99              Chinatown              40.715618              -73.994279   
106             Chinatown              40.715618              -73.994279   
107             Chinatown              40.715618              -73.994279   
112             Chinatown              40.715618              -73.994279   
116             Chinatown              40.715618              -73.994279   
117             Chinatown              40.715618              -73.994279   
118             Chinatown              40.715618              -73.994279   
119             Chinatown              40.715618              -73.994279   
120             Chinatown              40.715618              -73.994279   
122    Washington Heights              40.851903              -73.936900   
125    Washington Heights              40.851903              -73.936900   
134    Washington Heights              40.851903              -73.936900   
137    Washington Heights              40.851903              -73.936900   
139    Washington Heights              40.851903              -73.936900   
143    Washington Heights              40.851903              -73.936900   
147    Washington Heights              40.851903              -73.936900   
148    Washington Heights              40.851903              -73.936900   
151    Washington Heights              40.851903              -73.936900   
152    Washington Heights              40.851903              -73.936900   
158    Washington Heights              40.851903             

In [34]:
manhattan_reduced.reset_index()

index         Neighborhood  Neighborhood Latitude  \
0         9          Marble Hill              40.876551   
1        24            Chinatown              40.715618   
2        27            Chinatown              40.715618   
3        29            Chinatown              40.715618   
4        32            Chinatown              40.715618   
5        35            Chinatown              40.715618   
6        39            Chinatown              40.715618   
7        41            Chinatown              40.715618   
8        44            Chinatown              40.715618   
9        47            Chinatown              40.715618   
10       54            Chinatown              40.715618   
11       55            Chinatown              40.715618   
12       59            Chinatown              40.715618   
13       62            Chinatown              40.715618   
14       63            Chinatown              40.715618   
15       66            Chinatown              40.715618   
16       67            Chinatown              40.715618   
17       68            Chinatown              40.715618   
18       69            Chinatown              40.715618   
19       70            Chinatown              40.715618   
20       72            Chinatown              40.715618   
21       76            Chinatown              40.715618   
22       78            Chinatown              40.715618   
23       79            Chinatown              40.715618   
24       81            Chinatown              40.715618   
25       84            Chinatown              40.715618   
26       85            Chinatown              40.715618   
27       88            Chinatown              40.715618   
28       91            Chinatown              40.715618   
29       92            Chinatown              40.715618   
30       95            Chinatown              40.715618   
31       97            Chinatown              40.715618   
32       99            Chinatown              40.715618   
33      106            Chinatown              40.715618   
34      107            Chinatown              40.715618   
35      112            Chinatown              40.715618   
36      116            Chinatown              40.715618   
37      117            Chinatown              40.715618   
38      118            Chinatown              40.715618   
39      119            Chinatown              40.715618   
40      120            Chinatown              40.715618   
41      122   Washington Heights              40.851903   
42      125   Washington Heights              40.851903   
43      134   Washington Heights              40.851903   
44      137   Washington Heights              40.851903   
45      139   Washington Heights              40.851903   
46      143   Washington Heights              40.851903   
47      147   Washington Heights              40.851903   
48      148   Washington Heights              40.851903   
49      151   Washington Heights              40.851903   
50      152   Washington Heights              40.851903   
51      158   Washington Heights              40.851903   
52      160   Washington Heights              40.851903   
53      161   Washington Heights              40.851903   
54      162   Washington Heights              40.851903   
55      165   Washington Heights              40.851903   
56      171   Washington Heights              40.851903   
57      172   Washington Heights              40.851903   
58      173   Washington Heights              40.851903   
59      175   Washington Heights              40.851903   
60      176   Washington Heights              40.851903   
61      181   Washington Heights              40.851903   
62      203   Washington Heights              40.851903   
63      210               Inwood              40.867684   
64      216               Inwood              40.867684   
65      217               Inwood              40.867684   
66      225               Inwood              40.8676

In [78]:
manhattan_reduced['Venue Category'].unique()

array(['Restaurant', 'Bar', 'Hotel', 'Café', 'Gym', 'Shop'], dtype=object)

In [35]:
safe_d = manhattan_reduced

#### we are going now to construct our DataFrame that would be classified in the fianl step

In [36]:
#extract neighborhood names with coordinate of the venues
neigh = manhattan_reduced[['Neighborhood' , 'Venue Latitude' , 'Venue Longitude' ]]
neigh

Neighborhood  Venue Latitude  Venue Longitude
9             Marble Hill       40.877885       -73.905873
24              Chinatown       40.717010       -73.993530
27              Chinatown       40.714476       -73.992036
29              Chinatown       40.717278       -73.994177
32              Chinatown       40.716735       -73.995752
35              Chinatown       40.715232       -73.997263
39              Chinatown       40.714459       -73.991546
41              Chinatown       40.714830       -73.991719
44              Chinatown       40.714713       -73.991538
47              Chinatown       40.714763       -73.991455
54              Chinatown       40.717639       -73.995187
55              Chinatown       40.718291       -73.992584
59              Chinatown       40.714303       -73.991796
62              Chinatown       40.718254       -73.995930
63              Chinatown       40.714468       -73.991589
66              Chinatown       40.718145       -73.991988
67              Chinatown       40.715881       -73.997209
68              Chinatown       40.717560       -73.992580
69              Chinatown       40.715720       -73.990332
70              Chinatown       40.718215       -73.994345
72              Chinatown       40.715661       -73.996693
76              Chinatown       40.715876       -73.990467
78              Chinatown       40.717824       -73.992801
79              Chinatown       40.715004       -73.991010
81              Chinatown       40.713974       -73.990868
84              Chinatown       40.715039       -73.996941
85              Chinatown       40.715787       -73.996905
88              Chinatown       40.714368       -73.997869
91              Chinatown       40.714198       -73.990157
92              Chinatown       40.713618       -73.995978
95              Chinatown       40.718316       -73.991885
97              Chinatown       40.717722       -73.990497
99              Chinatown       40.717605       -73.995304
106             Chinatown       40.717847       -73.990358
107             Chinatown       40.718057       -73.992060
112             Chinatown       40.714512       -73.998235
116             Chinatown       40.716196       -73.998303
117             Chinatown       40.714423       -73.998904
118             Chinatown       40.713992       -73.990169
119             Chinatown       40.717801       -73.996846
120             Chinatown       40.715545       -73.998137
122    Washington Heights       40.851255       -73.939473
125    Washington Heights       40.851423       -73.939761
134    Washington Heights       40.850693       -73.936568
137    Washington Heights       40.851251       -73.940343
139    Washington Heights       40.855226       -73.937793
143    Washington Heights       40.855234       -73.937284
147    Washington Heights       40.850267       -73.933145
148    Washington Heights       40.855222       -73.936967
151    Washington Heights       40.854334       -73.933677
152    Washington Heights       40.848059       -73.937645
158    Washington Heights       40.850447       -73.933030
160    Washington Heights       40.855309       -73.937832
161    Washington Heights       40.850740       -73.932470
162    Washington Heights       40.849725       -73.936259
165    Washington Heights       40.851255       -73.939652
171    Washington Heights       40.851332       -73.931864
172    Washington Heights       40.847615       -73.938143
173    Washington Heights       40.851110       -73.939220
175    Washington Heights       40.855039       -73.937031
176    Washington Heights       40.848216       -73.938164
181    Washington Heights       40.848210       -73.937743
203    Washington Heights       40.851715       -73.932571
210                Inwood       40.867334       -73.920863
216                Inwood       40.866297       -73.919626
217                Inwood       40.867816       -73.920739
225                Inwood       40.866357       -73.925012
2

In [37]:
neigh_loc= neigh.groupby('Neighborhood').mean()
neigh_loc

Venue Latitude  Venue Longitude
Neighborhood                                        
Battery Park City         40.711156       -74.014930
Carnegie Hill             40.781950       -73.952236
Central Harlem            40.815332       -73.944001
Chelsea                   40.743490       -74.003115
Chinatown                 40.715887       -73.994153
Civic Center              40.716035       -74.007466
Clinton                   40.759444       -73.994891
East Harlem               40.791412       -73.944637
East Village              40.727619       -73.983159
Financial District        40.706867       -74.009617
Flatiron                  40.739545       -73.990264
Gramercy                  40.738177       -73.982708
Greenwich Village         40.727784       -74.000757
Hamilton Heights          40.824180       -73.948783
Hudson Yards              40.756560       -73.997781
Inwood                    40.866709       -73.920928
Lenox Hill                40.768342       -73.958036
Lincoln Square            40.773991       -73.983408
Little Italy              40.719865       -73.996954
Lower East Side           40.718692       -73.984229
Manhattan Valley          40.798995       -73.966167
Manhattanville            40.815578       -73.958023
Marble Hill               40.876824       -73.906374
Midtown                   40.754438       -73.981762
Midtown South             40.747198       -73.987951
Morningside Heights       40.807520       -73.962366
Murray Hill               40.748706       -73.978510
Noho                      40.722751       -73.988455
Roosevelt Island          40.761257       -73.950634
Soho                      40.722298       -73.999215
Stuyvesant Town           40.728993       -73.977978
Sutton Place              40.760618       -73.964514
Tribeca                   40.720707       -74.008711
Tudor City                40.747644       -73.974269
Turtle Bay                40.753418       -73.969513
Upper East Side           40.775320       -73.959047
Upper West Side           40.785822       -73.975549
Washington Heights        40.851095       -73.936645
West Village              40.734088       -74.004960
Yorkville                 40.776602       -73.949793

In [38]:
manhattan_dim = pd.get_dummies(manhattan_reduced[['Venue Category']], prefix="", prefix_sep="")

In [39]:
manhattan_dim

Bar  Café  Gym  Hotel  Restaurant  Shop
9       0     0    0      0           1     0
24      0     0    0      0           1     0
27      0     0    0      0           1     0
29      0     0    0      0           1     0
32      0     0    0      0           1     0
35      0     0    0      0           1     0
39      0     0    0      0           1     0
41      0     0    0      0           1     0
44      0     0    0      0           1     0
47      0     0    0      0           1     0
54      0     0    0      0           1     0
55      0     0    0      0           1     0
59      0     0    0      0           1     0
62      0     0    0      0           1     0
63      0     0    0      0           1     0
66      0     0    0      0           1     0
67      0     0    0      0           1     0
68      0     0    0      0           1     0
69      0     0    0      0           1     0
70      0     0    0      0           1     0
72      0     0    0      0           1     0
76      0     0    0      0           1     0
78      0     0    0      0           1     0
79      0     0    0      0           1     0
81      0     0    0      0           1     0
84      0     0    0      0           1     0
85      0     0    0      0           1     0
88      0     0    0      0           1     0
91      0     0    0      0           1     0
92      0     0    0      0           1     0
95      0     0    0      0           1     0
97      0     0    0      0           1     0
99      0     0    0      0           1     0
106     0     0    0      0           1     0
107     0     0    0      0           1     0
112     0     0    0      0           1     0
116     0     0    0      0           1     0
117     0     0    0      0           1     0
118     0     0    0      0           1     0
119     0     0    0      0           1     0
120     0     0    0      0           1     0
122     0     0    0      0           1     0
125     0     0    0      0           1     0
134     0     0    0      0           1     0
137     0     0    0      0           1     0
139     0     0    0      0           1     0
143     0     0    0      0           1     0
147     0     0    0      0           1     0
148     0     0    0      0           1     0
151     0     0    0      0           1     0
152     0     0    0      0           1     0
158     0     0    0      0           1     0
160     0     0    0      0           1     0
161     0     0    0      0           1     0
162     0     0    0      0           1     0
165     0     0    0      0           1     0
171     0     0    0      0           1     0
172     0     0    0      0           1     0
173     0     0    0      0           1     0
175     0     0    0      0           1     0
176     0     0    0      0           1     0
181     0     0    0      0           1     0
203     0     0    0      0           1     0
210     0     0    0      0           1     0
216     0     0    0      0           1     0
217     0     0    0      0           1     0
225     0     0    0      0           1     0
226     0     0    0      0           1     0
230     0     0    0      0           1     0
232     0     0    0      0           1     0
236     0     0    0      0           1     0
237     0     0    0      0           1     0
239     0     0    0      0           1     0
240     0     0    0      0           1     0
242     0     0    0      0           1     0
245     0     0    0      0           1     0
246     0     0    0      0           1     0
247     0     0    0      0           1     0
250     0     0    0      0           1     0
255     0     0    0      0           1     0
259     0     0    0      0           1     0
266     0     0    0      0           1     0
270     0     0    0      0           1     0
273     0     0    0      0           1     0
275     0     0    0      0           1     0
280     0     0    0      0           1     0
281 

In [40]:
manhattan_pre_final = manhattan_dim

In [41]:
manhattan_pre_final['Neighborhood'] = manhattan_reduced['Neighborhood']

In [42]:
manhattan_pre_final

Bar  Café  Gym  Hotel  Restaurant  Shop         Neighborhood
9       0     0    0      0           1     0          Marble Hill
24      0     0    0      0           1     0            Chinatown
27      0     0    0      0           1     0            Chinatown
29      0     0    0      0           1     0            Chinatown
32      0     0    0      0           1     0            Chinatown
35      0     0    0      0           1     0            Chinatown
39      0     0    0      0           1     0            Chinatown
41      0     0    0      0           1     0            Chinatown
44      0     0    0      0           1     0            Chinatown
47      0     0    0      0           1     0            Chinatown
54      0     0    0      0           1     0            Chinatown
55      0     0    0      0           1     0            Chinatown
59      0     0    0      0           1     0            Chinatown
62      0     0    0      0           1     0            Chinatown
63      0     0    0      0           1     0            Chinatown
66      0     0    0      0           1     0            Chinatown
67      0     0    0      0           1     0            Chinatown
68      0     0    0      0           1     0            Chinatown
69      0     0    0      0           1     0            Chinatown
70      0     0    0      0           1     0            Chinatown
72      0     0    0      0           1     0            Chinatown
76      0     0    0      0           1     0            Chinatown
78      0     0    0      0           1     0            Chinatown
79      0     0    0      0           1     0            Chinatown
81      0     0    0      0           1     0            Chinatown
84      0     0    0      0           1     0            Chinatown
85      0     0    0      0           1     0            Chinatown
88      0     0    0      0           1     0            Chinatown
91      0     0    0      0           1     0            Chinatown
92      0     0    0      0           1     0            Chinatown
95      0     0    0      0           1     0            Chinatown
97      0     0    0      0           1     0            Chinatown
99      0     0    0      0           1     0            Chinatown
106     0     0    0      0           1     0            Chinatown
107     0     0    0      0           1     0            Chinatown
112     0     0    0      0           1     0            Chinatown
116     0     0    0      0           1     0            Chinatown
117     0     0    0      0           1     0            Chinatown
118     0     0    0      0           1     0            Chinatown
119     0     0    0      0           1     0            Chinatown
120     0     0    0      0           1     0            Chinatown
122     0     0    0      0           1     0   Washington Heights
125     0     0    0      0           1     0   Washington Heights
134     0     0    0      0           1     0   Washington Heights
137     0     0    0      0           1     0   Washington Heights
139     0     0    0      0           1     0   Washington Heights
143     0     0    0      0           1     0   Washington Heights
147     0     0    0      0           1     0   Washington Heights
148     0     0    0      0           1     0   Washington Heights
151     0     0    0      0           1     0   Washington Heights
152     0     0    0      0           1     0   Washington Heights
158     0     0    0      0           1     0   Washington Heights
160     0     0    0      0           1     0   Washington Heights
161     0     0    0      0           1     0   Washington Heights
162     0     0    0      0           1     0   Washington Heights
165     0     0    0      0           1     0   Washington Heights
171     0     0    0      0           1     0   Washington Heights
172     0     0    0      0           1     0   Washington Heights
173     0     0    0      0           1     0   Washi

In [43]:
manhattan_pre_final.head()

Bar  Café  Gym  Hotel  Restaurant  Shop Neighborhood
9     0     0    0      0           1     0  Marble Hill
24    0     0    0      0           1     0    Chinatown
27    0     0    0      0           1     0    Chinatown
29    0     0    0      0           1     0    Chinatown
32    0     0    0      0           1     0    Chinatown

In [44]:
coll = manhattan_pre_final.pop("Neighborhood")
manhattan_pre_final.insert(0,"Neighborhood",coll)

In [45]:
manhattan_pre_final.head()

Neighborhood  Bar  Café  Gym  Hotel  Restaurant  Shop
9   Marble Hill    0     0    0      0           1     0
24    Chinatown    0     0    0      0           1     0
27    Chinatown    0     0    0      0           1     0
29    Chinatown    0     0    0      0           1     0
32    Chinatown    0     0    0      0           1     0

In [46]:
safe_pre = manhattan_pre_final

### 

In [47]:
manhattan_mean = manhattan_pre_final.groupby('Neighborhood').mean().reset_index()
manhattan_mean

Neighborhood       Bar      Café       Gym     Hotel  Restaurant  \
0     Battery Park City  0.041667  0.000000  0.166667  0.208333    0.166667   
1         Carnegie Hill  0.111111  0.074074  0.111111  0.018519    0.388889   
2        Central Harlem  0.206897  0.034483  0.068966  0.000000    0.517241   
3               Chelsea  0.096154  0.038462  0.038462  0.038462    0.403846   
4             Chinatown  0.134328  0.000000  0.000000  0.014925    0.597015   
5          Civic Center  0.105263  0.017544  0.140351  0.105263    0.403509   
6               Clinton  0.163636  0.018182  0.163636  0.072727    0.400000   
7           East Harlem  0.100000  0.050000  0.050000  0.000000    0.750000   
8          East Village  0.250000  0.013158  0.000000  0.000000    0.500000   
9    Financial District  0.175439  0.052632  0.087719  0.052632    0.350877   
10             Flatiron  0.049180  0.032787  0.098361  0.000000    0.524590   
11             Gramercy  0.214286  0.035714  0.000000  0.035714    0.392857   
12    Greenwich Village  0.041667  0.055556  0.041667  0.013889    0.652778   
13     Hamilton Heights  0.189189  0.108108  0.000000  0.000000    0.513514   
14         Hudson Yards  0.062500  0.062500  0.187500  0.156250    0.406250   
15               Inwood  0.129032  0.096774  0.000000  0.000000    0.580645   
16           Lenox Hill  0.131148  0.049180  0.098361  0.000000    0.459016   
17       Lincoln Square  0.052632  0.105263  0.157895  0.026316    0.368421   
18         Little Italy  0.133333  0.100000  0.016667  0.050000    0.400000   
19      Lower East Side  0.071429  0.107143  0.000000  0.000000    0.571429   
20     Manhattan Valley  0.161290  0.032258  0.032258  0.000000    0.516129   
21       Manhattanville  0.080000  0.040000  0.040000  0.000000    0.680000   
22          Marble Hill  0.000000  0.000000  0.250000  0.000000    0.125000   
23              Midtown  0.039216  0.039216  0.078431  0.117647    0.352941   
24        Midtown South  0.032258  0.032258  0.080645  0.112903    0.500000   
25  Morningside Heights  0.000000  0.111111  0.000000  0.000000    0.555556   
26          Murray Hill  0.119403  0.029851  0.104478  0.059701    0.552239   
27                 Noho  0.150000  0.033333  0.033333  0.083333    0.500000   
28     Roosevelt Island  0.000000  0.000000  0.222222  0.000000    0.333333   
29                 Soho  0.076923  0.057692  0.038462  0.057692    0.461538   
30      Stuyvesant Town  0.500000  0.000000  0.250000  0.000000    0.000000   
31         Sutton Place  0.107143  0.000000  0.125000  0.035714    0.482143   
32              Tribeca  0.204545  0.068182  0.045455  0.045455    0.500000   
33           Tudor City  0.041667  0.104167  0.083333  0.020833    0.604167   
34           Turtle Bay  0.135593  0.033898  0.050847  0.033898    0.610169   
35      Upper East Side  0.081633  0.020408  0.081633  0.081633    0.448980   
36      Upper West Side  0.164179  0.059701  0.029851  0.014925    0.552239   
37   Washington Heights  0.042553  0.148936  0.063830  0.000000    0.468085   
38         West Village  0.206897  0.017241  0.017241  0.000000    0.551724   
39            Yorkville  0.125000  0.015625  0.125000  0.000000    0.468750   

        Shop  
0   0.416667  
1   0.296296  
2   0.172414  
3   0.384615  
4   0.253731  
5   0.228070  
6   0.181818  
7   0.050000  
8   0.236842  
9   0.280702  
10  0.295082  
11  0.321429  
12  0.194444  
13  0.189189  
14  0.125000  
15  0.193548  
16  0.262295  
17  0.289474  
18  0.300000  
19  0.250000  
20  0.258065  
21  0.160000  
22  0.625000  
23  0.372549  
24  0.241935  
25  0.333333  
26  0.134328  
27  0.200000  
28  0.444444  
29  0.307692  
30  0.250000  
31  0.250000  
32  0.136364  
33  0.145833  
34  0.135593  
35  0.285714  
36  0.179104  
37  0.276596  
38  0.206897  
39  0.265625

#### here we could see bellow the top 3 visited venues in each neighborhood, with this information we could set a threshold convenient with the client input, for exemple, if he chose to make a "Bar" we mention the neighborhoods where Bar is not in the top 3  of the most visited of that place.

In [48]:
num_top_venues = 3

for hood in manhattan_mean['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_mean[manhattan_mean['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
   venue  freq
0   Shop  0.42
1  Hotel  0.21
2    Gym  0.17


----Carnegie Hill----
        venue  freq
0  Restaurant  0.39
1        Shop  0.30
2         Bar  0.11


----Central Harlem----
        venue  freq
0  Restaurant  0.52
1         Bar  0.21
2        Shop  0.17


----Chelsea----
        venue  freq
0  Restaurant  0.40
1        Shop  0.38
2         Bar  0.10


----Chinatown----
        venue  freq
0  Restaurant  0.60
1        Shop  0.25
2         Bar  0.13


----Civic Center----
        venue  freq
0  Restaurant  0.40
1        Shop  0.23
2         Gym  0.14


----Clinton----
        venue  freq
0  Restaurant  0.40
1        Shop  0.18
2         Bar  0.16


----East Harlem----
        venue  freq
0  Restaurant  0.75
1         Bar  0.10
2        Café  0.05


----East Village----
        venue  freq
0  Restaurant  0.50
1         Bar  0.25
2        Shop  0.24


----Financial District----
        venue  freq
0  Restaurant  0.35
1        Shop  0.28
2         Ba

#### to better see this distribution, i'll classify the data into 6 categories with KNN and plot it into a map

In [49]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
num_top_venues = 6

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_mean['Neighborhood']

for ind in np.arange(manhattan_mean.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_mean.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Shop                 Hotel   
1      Carnegie Hill            Restaurant                  Shop   
2     Central Harlem            Restaurant                   Bar   
3            Chelsea            Restaurant                  Shop   
4          Chinatown            Restaurant                  Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant                   Gym                   Bar   
1                   Gym                   Bar                  Café   
2                  Shop                   Gym                  Café   
3                   Bar                 Hotel                   Gym   
4                   Bar                 Hotel                   Gym   

  6th Most Common Venue  
0                  Café  
1                 Hotel  
2                 Hotel  
3                  Café  
4                  Café

In [51]:
v_sorted = neighborhoods_venues_sorted

In [52]:
# set number of clusters
kclusters = 6

manhattan_grouped_clustering = manhattan_mean.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 0, 2, 0, 2, 5, 5, 4, 2, 0], dtype=int32)

In [53]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [54]:
neighborhoods_venues_sorted

Cluster Labels         Neighborhood 1st Most Common Venue  \
0                3    Battery Park City                  Shop   
1                0        Carnegie Hill            Restaurant   
2                2       Central Harlem            Restaurant   
3                0              Chelsea            Restaurant   
4                2            Chinatown            Restaurant   
5                5         Civic Center            Restaurant   
6                5              Clinton            Restaurant   
7                4          East Harlem            Restaurant   
8                2         East Village            Restaurant   
9                0   Financial District            Restaurant   
10               0             Flatiron            Restaurant   
11               0             Gramercy            Restaurant   
12               4    Greenwich Village            Restaurant   
13               2     Hamilton Heights            Restaurant   
14               5         Hudson Yards            Restaurant   
15               2               Inwood            Restaurant   
16               0           Lenox Hill            Restaurant   
17               0       Lincoln Square            Restaurant   
18               0         Little Italy            Restaurant   
19               2      Lower East Side            Restaurant   
20               2     Manhattan Valley            Restaurant   
21               4       Manhattanville            Restaurant   
22               3          Marble Hill                  Shop   
23               0              Midtown                  Shop   
24               0        Midtown South            Restaurant   
25               0  Morningside Heights            Restaurant   
26               2          Murray Hill            Restaurant   
27               2                 Noho            Restaurant   
28               3     Roosevelt Island                  Shop   
29               0                 Soho            Restaurant   
30               1      Stuyvesant Town                   Bar   
31               0         Sutton Place            Restaurant   
32               2              Tribeca            Restaurant   
33               4           Tudor City            Restaurant   
34               4           Turtle Bay            Restaurant   
35               0      Upper East Side            Restaurant   
36               2      Upper West Side            Restaurant   
37               0   Washington Heights            Restaurant   
38               2         West Village            Restaurant   
39               0            Yorkville            Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Hotel            Restaurant                   Gym   
1                   Shop                   Gym                   Bar   
2                    Bar                  Shop                   Gym   
3                   Shop                   Bar                 Hotel   
4                   Shop                   Bar                 Hotel   
5                   Shop                   Gym                 Hotel   
6                   Shop                   Gym                   Bar   
7                    Bar                  Shop                   Gym   
8                    Bar                  Shop                  Café   
9                   Shop                   Bar                   Gym   
10                  Shop                   Gym                   Bar   
11                  Shop                   Bar                 Hotel   
12                  Shop                  Café                   Gym   
13                  Shop                   Bar                  Café   
14                   Gym                 Hotel                  Shop   
15                  Shop                   Bar                  Café   
16                  Shop                   Bar                   Gym   
17                  Shop                  

In [55]:
manhattan_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               3   
1  Manhattan           Chinatown  40.715618 -73.994279               2   
2  Manhattan  Washington Heights  40.851903 -73.936900               0   
3  Manhattan              Inwood  40.867684 -73.921210               2   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               2   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Shop                   Gym            Restaurant   
1            Restaurant                  Shop                   Bar   
2            Restaurant                  Shop                  Café   
3            Restaurant                  Shop                   Bar   
4            Restaurant                  Shop                   Bar   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  
0                 Hotel                  Café                   Bar  
1                 Hotel                   Gym                  Café  
2                   Gym                   Bar                 Hotel  
3                  Café                 Hotel                   Gym  
4                  Café                 Hotel                   Gym

In [56]:
manhattan_merged.shape

(40, 11)

In [57]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


In [58]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### we could see places disturbtion along with density of categories, for exemple Cluster 3 dedicated for places where Shop are more often visited, Cluster 0 is where Restaurant are more visited ... along with the knowledge the less visited venues.

In [59]:
# Now we'll build our Final DataFrame that we'll test the client input on

#extracting from the "manhattan_merged" the top 3 visisted venues with their location and names
final_df = manhattan_merged[['Neighborhood','Latitude','Longitude',"1st Most Common Venue", "2nd Most Common Venue", "3rd Most Common Venue"]]

In [60]:
final_df

Neighborhood   Latitude  Longitude 1st Most Common Venue  \
0           Marble Hill  40.876551 -73.910660                  Shop   
1             Chinatown  40.715618 -73.994279            Restaurant   
2    Washington Heights  40.851903 -73.936900            Restaurant   
3                Inwood  40.867684 -73.921210            Restaurant   
4      Hamilton Heights  40.823604 -73.949688            Restaurant   
5        Manhattanville  40.816934 -73.957385            Restaurant   
6        Central Harlem  40.815976 -73.943211            Restaurant   
7           East Harlem  40.792249 -73.944182            Restaurant   
8       Upper East Side  40.775639 -73.960508            Restaurant   
9             Yorkville  40.775930 -73.947118            Restaurant   
10           Lenox Hill  40.768113 -73.958860            Restaurant   
11     Roosevelt Island  40.762160 -73.949168                  Shop   
12      Upper West Side  40.787658 -73.977059            Restaurant   
13       Lincoln Square  40.773529 -73.985338            Restaurant   
14              Clinton  40.759101 -73.996119            Restaurant   
15              Midtown  40.754691 -73.981669                  Shop   
16          Murray Hill  40.748303 -73.978332            Restaurant   
17              Chelsea  40.744035 -74.003116            Restaurant   
18    Greenwich Village  40.726933 -73.999914            Restaurant   
19         East Village  40.727847 -73.982226            Restaurant   
20      Lower East Side  40.717807 -73.980890            Restaurant   
21              Tribeca  40.721522 -74.010683            Restaurant   
22         Little Italy  40.719324 -73.997305            Restaurant   
23                 Soho  40.722184 -74.000657            Restaurant   
24         West Village  40.734434 -74.006180            Restaurant   
25     Manhattan Valley  40.797307 -73.964286            Restaurant   
26  Morningside Heights  40.808000 -73.963896            Restaurant   
27             Gramercy  40.737210 -73.981376            Restaurant   
28    Battery Park City  40.711932 -74.016869                  Shop   
29   Financial District  40.707107 -74.010665            Restaurant   
30        Carnegie Hill  40.782683 -73.953256            Restaurant   
31                 Noho  40.723259 -73.988434            Restaurant   
32         Civic Center  40.715229 -74.005415            Restaurant   
33        Midtown South  40.748510 -73.988713            Restaurant   
34         Sutton Place  40.760280 -73.963556            Restaurant   
35           Turtle Bay  40.752042 -73.967708            Restaurant   
36           Tudor City  40.746917 -73.971219            Restaurant   
37      Stuyvesant Town  40.731000 -73.974052                   Bar   
38             Flatiron  40.739673 -73.990947            Restaurant   
39         Hudson Yards  40.756658 -74.000111            Restaurant   

   2nd Most Common Venue 3rd Most Common Venue  
0                    Gym            Restaurant  
1                   Shop                   Bar  
2                   Shop                  Café  
3                   Shop                   Bar  
4                   Shop                   Bar  
5                   Shop                   Bar  
6                    Bar                  Shop  
7                    Bar                  Shop  
8                   Shop                 Hotel  
9                   Shop                   Gym  
10                  Shop                   Bar  
11            Restaurant                   Gym  
12                  Shop                   Bar  
13                  Shop                   Gym  
14                  Shop                   Gym  
15            Restaurant                 Hotel  
16                  Shop                   Bar  
17                  Shop                   Bar  
18                  Shop                  Café  
19                   Bar                  Shop  
20                  Shop                  Café  
21                   

In [61]:
# now we'll make our final function to determine which places are better to make a business according to the client input

def adviceMe(my_choice):
    ar = np.array([])
    ar = np.append(ar ,final_df[
    (final_df['1st Most Common Venue'].values != my_choice) &
    (final_df['2nd Most Common Venue'].values != my_choice) &
    (final_df['3rd Most Common Venue'].values != my_choice) ].index )
   
    return final_df.iloc[ar,]
    
    
    
    

In [66]:
# let's try 
input = "Gym"

target_df = adviceMe(input)
target_df

Neighborhood   Latitude  Longitude 1st Most Common Venue  \
1             Chinatown  40.715618 -73.994279            Restaurant   
2    Washington Heights  40.851903 -73.936900            Restaurant   
3                Inwood  40.867684 -73.921210            Restaurant   
4      Hamilton Heights  40.823604 -73.949688            Restaurant   
5        Manhattanville  40.816934 -73.957385            Restaurant   
6        Central Harlem  40.815976 -73.943211            Restaurant   
7           East Harlem  40.792249 -73.944182            Restaurant   
8       Upper East Side  40.775639 -73.960508            Restaurant   
10           Lenox Hill  40.768113 -73.958860            Restaurant   
12      Upper West Side  40.787658 -73.977059            Restaurant   
15              Midtown  40.754691 -73.981669                  Shop   
16          Murray Hill  40.748303 -73.978332            Restaurant   
17              Chelsea  40.744035 -74.003116            Restaurant   
18    Greenwich Village  40.726933 -73.999914            Restaurant   
19         East Village  40.727847 -73.982226            Restaurant   
20      Lower East Side  40.717807 -73.980890            Restaurant   
21              Tribeca  40.721522 -74.010683            Restaurant   
22         Little Italy  40.719324 -73.997305            Restaurant   
23                 Soho  40.722184 -74.000657            Restaurant   
24         West Village  40.734434 -74.006180            Restaurant   
25     Manhattan Valley  40.797307 -73.964286            Restaurant   
26  Morningside Heights  40.808000 -73.963896            Restaurant   
27             Gramercy  40.737210 -73.981376            Restaurant   
28    Battery Park City  40.711932 -74.016869                  Shop   
29   Financial District  40.707107 -74.010665            Restaurant   
31                 Noho  40.723259 -73.988434            Restaurant   
33        Midtown South  40.748510 -73.988713            Restaurant   
35           Turtle Bay  40.752042 -73.967708            Restaurant   
36           Tudor City  40.746917 -73.971219            Restaurant   

   2nd Most Common Venue 3rd Most Common Venue  
1                   Shop                   Bar  
2                   Shop                  Café  
3                   Shop                   Bar  
4                   Shop                   Bar  
5                   Shop                   Bar  
6                    Bar                  Shop  
7                    Bar                  Shop  
8                   Shop                 Hotel  
10                  Shop                   Bar  
12                  Shop                   Bar  
15            Restaurant                 Hotel  
16                  Shop                   Bar  
17                  Shop                   Bar  
18                  Shop                  Café  
19                   Bar                  Shop  
20                  Shop                  Café  
21                   Bar                  Shop  
22                  Shop                   Bar  
23                  Shop                   Bar  
24                  Shop                   Bar  
25                  Shop                   Bar  
26                  Shop                  Café  
27                  Shop                   Bar  
28                 Hotel            Restaurant  
29                  Shop                   Bar  
31                  Shop                   Bar  
33                  Shop                 Hotel  
35                  Shop                   Bar  
36                  Shop                  Café

#### Here we could see an exemple for trying to choose a business as Gym, we eliminated the places where Gym is one of the top visited venues


In [79]:

#Let's polt the places where the licent want to build a Bar
input = "Bar"

target_df = adviceMe(input)
target_df.head()


Neighborhood   Latitude  Longitude 1st Most Common Venue  \
0          Marble Hill  40.876551 -73.910660                  Shop   
2   Washington Heights  40.851903 -73.936900            Restaurant   
8      Upper East Side  40.775639 -73.960508            Restaurant   
9            Yorkville  40.775930 -73.947118            Restaurant   
11    Roosevelt Island  40.762160 -73.949168                  Shop   

   2nd Most Common Venue 3rd Most Common Venue  
0                    Gym            Restaurant  
2                   Shop                  Café  
8                   Shop                 Hotel  
9                   Shop                   Gym  
11            Restaurant                   Gym

In [70]:
target_df.shape


(19, 6)

##### so we got 19 places where we could build a Bar 


In [75]:
#Let's plot them

# create map of Manhattan using latitude and longitude values
Bar_map = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(target_df['Latitude'], target_df['Longitude'],  target_df['Neighborhood']):
    label = '{}, Build a {}'.format(neighborhood , input)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(Bar_map)  
    
Bar_map

In [76]:
### here is it, the best places where u can build a Bar

#### we can change the threshold insted of 3 top visited venues to narrow the search or make it flatter